# Part 1 - Implementation of the basic functionality for Evolutionary Algorithms

This notebook has been developed in a way that allows the basic methods (like fitness and decode) of the GA to be redefined and overwritten with the new methods. So you may notice some strange results, or even errors, if you run the notebook in the wrong order (bottom to top).

However, each section is well documented, and as long as the first 3 code blocks are run then all of the others should work also, but bear in mind that code blocks like block 6 - (2. Hyper-parameter Analysis) are required to be run before the code blocks following them can be run.

This notebook does a lot of computation and takes around 10 minutes to fully execute (on a fast PC), feel free to change the numberOfGenerations specifically for the jigsaw GA (as it is run with 40,000 currently) and numberOfRuns, for the hyper-parameter analysis part, around 100-200 still nets good results.


## 1.2 >> Task definition
### Genetic algorithm hyper-parameters

In [11]:
#Increases the display width of the notebook
from IPython.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [14]:
import random as rnd
import timeit
import sys
import math

def resetHyperParameters():
    """Sets/resets the default values for the hyper parameters,
    using global variables for ease of use as these values change from within other functions"""
    
    global populationSize, numberOfGenerations, numberOfTournament, crossoverRate, mutationRate
    
    populationSize = 20
    numberOfGenerations = 100
    numberOfTournament = 2
    
    crossoverRate = 0.7
    mutationRate = 0.01 #mutation rate per bit

def printHyperParameters():
    """Prints the hyper-parameters """
    
    print("Hyper-parameters:")
    print("Population size:", populationSize)
    print("Number of generations:", numberOfGenerations)
    print("Number of individuals in tournament selection:", numberOfTournament)
    print("Crossover rate:", crossoverRate)
    print("Mutation rate (per bit):", mutationRate, "\n")

### General genetic algorithm functions
__*initialPopulation()*__<br>
Creates the initial population based on 'populationSize'.

__*generateRandomChromosome()*__<br>
Creates a random chromosome of size 'numberOfBits' for the initial population.

__*crossover()*__<br>
Selects 2 chromosomes using tournament selection and chooses a random cut point,
    merges the part of chromosome 1 from the start to the crossover point and the part of chromosome 2 from the crossover point to the end as the right part. Chromosome1 is exclusive of crossover point and chromosome2 inclusive of crossover point.

__*mutateChromosome(chromosome)*__<br>
Has a chance 'mutationRate' to mutate (flip) every bit of a given 'chromosome'.

__*tournamentSelection()*__<br>
Selects 'numberOfTournament' random chromosomes and returns either the biggest fitness score.

In [15]:
def initialPopulation():
    """Creates the initial population based on 'populationSize'"""
    
    population = [""] * populationSize
    
    for i in range(populationSize):
        population[i] = generateRandomChromosome()
        
    return population

    
def generateRandomChromosome():
    """Creates a random chromosome of size 'numberOfBits' for the initial population"""
    
    newChromosome = ""
    
    for i in range(numberOfBits):
        if (rnd.random() < 0.5):
            newChromosome += "1"
        else:
            newChromosome += "0"
    
    return newChromosome


def crossover():
    """Selects 2 chromosomes using tournament selection and chooses a random cut point,
    merges the part of chromosome 1 from the start to the crossover point
    and the part of chromosome 2 from the crossover point to the end as the right part
    chromosome1 exclusive of crossover point
    chromosome2 inclusive of crossover point"""
    
    chromosome1 = tournamentSelection()
    chromosome2 = tournamentSelection()
    crossoverPoint = rnd.randint(1, numberOfBits - 1)
    
    return chromosome1[:crossoverPoint] + chromosome2[crossoverPoint:]
    
    
def mutateChromosome(chromosome):
    """Has a chance 'mutationRate' to mutate (flip) every bit of a given 'chromosome'"""
    
    mutatedChromosome = ""
    
    for bit in chromosome:
        if (rnd.random() < mutationRate):
            mutatedChromosome += "1" if bit == "0" else "0"
        else:
            mutatedChromosome += bit
            
    return mutatedChromosome
    
    
def tournamentSelection():
    """Selects 'numberOfTournament' random chromosomes and returns the biggest score"""
    
    tournament = [()] * numberOfTournament
    
    for i in range(numberOfTournament):
        randomIndex = rnd.randint(0, populationSize - 1)
        tournament[i] = (population[randomIndex], fitnessList[randomIndex])
    
    #Gets the max chromosome by comparing using the second element (f[1])
    #of each entry (fitness), and getting the first element ([0]) of the resulting tuple (chromosome)
    return max(tournament, key=lambda f: f[1])[0]

## 1.3 >> Combinatorial optimisation problems
#### <ins>Main genetic algorithm method</ins>
__*runGA(displayOutput = True, breakout = False, displayASCII = True)*__<br>
Runs the GA based on the current hyper-parameters.

__*getWorstChromosomeIndex()*__<br>
Returns the index of the worst chromosome in the population.

__*printResults(bestChromosome, reachedAtGeneration)*__<br>
Prints the result of the GA run.

In [16]:
def runGA(displayOutput = True, breakout = False, displayASCII = True):
    """Runs the GA based on the current hyper-parameters,
    
    Args:
    displayOutput boolean - if false GA does not print anything to the terminal,
                            this is for the Hyper-parameter analysis.
    breakout boolean - true if the GA should stop once the perfect solution has been found
                       false for the GA to continue until all generations have completed.
    
    Returns:
    Integer - The generation at which the best solution was found at.
    Float/Integer - The fitness score of the best solution.
    Integer - The fitness evaluation count
    String - The best chromosome
    """
    
    if (displayOutput):
        print("Start of GA\n")
        printHyperParameters()

    #Using global as the other functions use this variable
    global fitnessEvaluationCount
    fitnessEvaluationCount = 0

    global population
    population = initialPopulation()
    
    bestChromosomeFitness = 0
    bestChromosome = ""
    reachedAtGeneration = 0
    

    #Using a seperate list for storing the fitness values
    #reduces the amount of fitness evaluations by a factor of around 10+
    global fitnessList
    fitnessList = [0] * populationSize
    for i in range(populationSize):
        fitnessList[i] = fitness(population[i])
    
    
    
    #Main loop
    for generation in range(numberOfGenerations):

        #For each chromosome
        for chromosome in population:

            if (rnd.random() < crossoverRate):
                newChromosome = crossover()
            else:
                newChromosome = tournamentSelection()

            newChromosome = mutateChromosome(newChromosome)

            
            #Replace the worst chromosome with the new chromosome
            worstChromosomeIndex = getWorstChromosomeIndex()
            
            population[worstChromosomeIndex] = newChromosome
            fitnessList[worstChromosomeIndex] = fitness(newChromosome)
            


        #Generation statistics
        totalFitness = 0
        for index in range(populationSize):
            chromosomeFitness = fitnessList[index]
            totalFitness += chromosomeFitness

            #Update best chromosome
            if (chromosomeFitness > bestChromosomeFitness):
                bestChromosome = population[index]
                bestChromosomeFitness = chromosomeFitness
                reachedAtGeneration = generation

        averageFitness = totalFitness / populationSize
        
        if (displayOutput):
            print("Generation-{:<5d}    Average fitness: {:<20}    Best fitness: {:<20}"
                  .format(generation, averageFitness, bestChromosomeFitness))
            
        if breakout and bestChromosomeFitness == 85:
            break


    
    if (displayOutput):
        printResults(bestChromosome, reachedAtGeneration)
        
        if displayASCII:
            displayChromosome(bestChromosome)
        else:
            print(bestChromosome)

    if (displayOutput):
        print("\nEnd of GA")
    return reachedAtGeneration, fitness(bestChromosome), fitnessEvaluationCount, bestChromosome


def getWorstChromosomeIndex():
    """Returns the index of the worst chromosome in the population."""
    
    minFitness = 1_000_000_000
    worstChromosomeIndex = -1
    
    for index in range(populationSize):
        fitnessScore = fitnessList[index]

        if (fitnessScore < minFitness):
            minFitness = fitnessScore
            worstChromosomeIndex = index
    return worstChromosomeIndex


def printResults(bestChromosome, reachedAtGeneration):
    """Prints the result of the GA run."""
    
    print("\n\nSolutions sampled: {:,}".format(populationSize * numberOfGenerations))
    print("Search space: {:,}".format(pow(2, numberOfBits)))
    print("Fraction of search space explored: {}%"
          .format((populationSize * numberOfGenerations) / pow(2, numberOfBits)))
    print("Number of fitness evaluations:", fitnessEvaluationCount)
    
    print("\nBest chromosome:", fitness(bestChromosome))
    print("Reached at generation", reachedAtGeneration)
    print("Output:")

### 1. ASCII art
#### <ins>ASCII problem setup</ins>
__*fitness(chromosome)*__<br>
Evaluates the fitness score of a chromosome, which is the number of bits that match the ASCII bit string.
    
__*displayChromosome(chromosome)*__<br>
Displays the ASCII art for a given chromosome.
    
__*displayAllChromosomes()*__<br>
Displays the ASCII art of all chromosomes in 'population'.

In [17]:
#Variables to decode chromosomes
numberOfBitsPerRow = 17
numberOfRows = 5
numberOfBits = numberOfBitsPerRow * numberOfRows

#Encoded target binary pattern
ASCII = "0001111000001100000100001000101100010000000010001100010011100111111000011101001000010"



def fitness(chromosome):
    """Evaluates the fitness score of a chromosome, which is the number of bits
    that match the ASCII bit string"""
    
    global fitnessEvaluationCount
    fitnessEvaluationCount += 1
    score = 0
    
    for index in range(len(chromosome)):
        if (chromosome[index] == ASCII[index]):
            score+= 1
    
    return score


def displayChromosome(chromosome):
    """Displays the ASCII art for a given chromosome"""
    
    #For each row
    for r in range(numberOfRows):
        #For each 'column'
        for c in range(numberOfBitsPerRow):
            print(chromosome[numberOfBitsPerRow * r + 1 * c], end="")
        print()

    
def displayAllChromosomes():
    """Displays the ASCII art of all chromosomes in 'population'"""
    
    for chromosome in population:
        displayChromosome(chromosome)

resetHyperParameters()
runGA()

Start of GA

Hyper-parameters:
Population size: 20
Number of generations: 100
Number of individuals in tournament selection: 2
Crossover rate: 0.7
Mutation rate (per bit): 0.01 

Generation-0        Average fitness: 48.5                    Best fitness: 54                  
Generation-1        Average fitness: 51.4                    Best fitness: 57                  
Generation-2        Average fitness: 54.2                    Best fitness: 60                  
Generation-3        Average fitness: 58.35                   Best fitness: 62                  
Generation-4        Average fitness: 60.35                   Best fitness: 62                  
Generation-5        Average fitness: 61.75                   Best fitness: 63                  
Generation-6        Average fitness: 62.35                   Best fitness: 64                  
Generation-7        Average fitness: 63.35                   Best fitness: 64                  
Generation-8        Average fitness: 63.85           

(38,
 85,
 2022,
 '0001111000001100000100001000101100010000000010001100010011100111111000011101001000010')

### 1. Obervations of maximising/minimising the fitness function
With a maximised fitness function the end result should have the 'GA' part of the ascii art consitiing of 1's and the rest of the ascii art being 0's. e.g:<br>
```
00011110000011000
00100001000101100
01000000001000110
00100111001111110
00011101001000010
```

Whereas, with a minimised fitness function the resulting ASCII art would be the opposite, or the most incorrect with the given ASCII art specification, with the 'GA' part made up with 0's and the other charaters being 1's. e.g<br>
```
11100001111100111
11011110111010011
10111111110111001
11011000110000001
11100010110111101
```

Running the GA twice with the function maximised/minimised proves this.<br>
Maximised: fitness(ind) = sum over i of (ind[i] == ASCII[i])<br>
Minimised: fitness(ind) = sum over i of (ind[i] != ASCII[i]) (Not equal to ASCII)<br>

### 2. Hyper-parameter Analysis
#### <ins>Function to run the GA many times and outputs its statistics</ins>
The GA in this section breaks out of execution when the perfect solution is found; however, if the GA does not know what the 'perfect' solution is, the breakout can be set to False in the line runGA(displayOutput = False, breakout = True).<br><br>

The below Hyper-parameter analysis is with the GA breakout set to true. The differences are that the algorithms will run faster, and the average fitness evaluations will differ. With breakout set to false, the average fitness evaluations will be solutions sampled + population size + 1, meaning that the GA will have more redundant generations. Whereas, with breakout set to true, the average fitness evaluations will be based on the results from the running of the GAs.<br><br>

__*runAlgorithm()*__<br>
Runs the GA 'numberOfRuns' times, analyses the result of all runs and outputs them. It calls runGA(displayOutput = False) to not display the individual results of each time the GA is run.

In [18]:
def runAlgorithm():
    startTime = timeit.default_timer()
    
    numberOfRuns = 1000

    reachedAtGen_Total = 0
    numberCorrectSolutions = 0
    totalFitnessEvaluations = 0

    
    for i in range(numberOfRuns):
        run = runGA(displayOutput = False, breakout = True)
        
        totalFitnessEvaluations += run[2]

        if (run[1] == 85):
            numberCorrectSolutions += 1
            reachedAtGen_Total += run[0]
            
        #Displays progress as a percentage (removes once loop has completed)
        sys.stdout.write("\r%d%%" % ((i / (numberOfRuns - 1)) * 100))
        sys.stdout.flush()
    sys.stdout.write("\r" + " " * 4 + "\r")

    timeElapsed = timeit.default_timer() - startTime
    
    
    #Results
    print("Time taken to run {} algorithms: {:.2f} seconds".format(numberOfRuns, timeElapsed))
    print("Number of perfect solutions found: {}/{} - {:.2f}%"
          .format(numberCorrectSolutions, numberOfRuns, (numberCorrectSolutions / numberOfRuns) * 100))
    
    if numberCorrectSolutions == 0:
        print("Average perfect solution found at generation: {:.2f}/{}"
              .format(0, numberOfGenerations))
    else:
        print("Average perfect solution found at generation: {:.2f}/{}"
              .format(reachedAtGen_Total / numberCorrectSolutions, numberOfGenerations))
    
    print("Average fitness evaluations: {:.2f}".format(totalFitnessEvaluations / numberOfRuns))
    print()
    
    #Reset parameters to default when complete
    resetHyperParameters()

#### Analysing the population size:

In [19]:
print("Starting algorithms")
populationSize = 30
print("\n    Population size:", populationSize)
runAlgorithm()

populationSize = 20
print("\n    Population size:", populationSize)
runAlgorithm()

populationSize = 10
print("\n    Population size:", populationSize)
runAlgorithm()
print("Finished all algorithms")

Starting algorithms

    Population size: 30
Time taken to run 1000 algorithms: 18.32 seconds
Number of perfect solutions found: 999/1000 - 99.90%
Average perfect solution found at generation: 44.33/100
Average fitness evaluations: 1392.67


    Population size: 20
Time taken to run 1000 algorithms: 15.99 seconds
Number of perfect solutions found: 987/1000 - 98.70%
Average perfect solution found at generation: 57.11/100
Average fitness evaluations: 1194.10


    Population size: 10
Time taken to run 1000 algorithms: 11.80 seconds
Number of perfect solutions found: 578/1000 - 57.80%
Average perfect solution found at generation: 80.62/100
Average fitness evaluations: 904.74

Finished all algorithms


#### Results:
Looking at these results there are 4 different distinctions that can be made:<br>

__The higher the population size:__
- it takes longer to run
- it is more likely to find the perfect solution
- it will tend to find the perfect solution quicker
- it has more fitness evaluations<br><br>

__The lowest the population size:__
- it is quicker
- it is less likely to find the perfect solution
- it will normally take more generations to find the perfect solution
- it has less fitness evaluations
    
Selecting the best population size depends on the situation. For example, larger population size is more suitable when the problem prioritises finding the perfect solution. Conversely, a lower population size can be used if the priority is speed; however, it should be noted that it is more unlikely to find the perfect solution. For example, 20+ is a reasonable population size since it usually finds the perfect solution and runs quickly due to the reduced number of fitness evaluations.

#### Analysing the number of generations:

In [8]:
print("Starting algorithms")
numberOfGenerations = 200
print("\n    Number of generations:", numberOfGenerations)
runAlgorithm()

numberOfGenerations = 100
print("\n    Number of generations:", numberOfGenerations)
runAlgorithm()

numberOfGenerations = 50
print("\n    Number of generations:", numberOfGenerations)
runAlgorithm()
print("Finished all algorithms")

Starting algorithms

    Number of generations: 200
Time taken to run 1000 algorithms: 15.95 seconds
Number of perfect solutions found: 1000/1000 - 100.00%
Average perfect solution found at generation: 58.27/200
Average fitness evaluations: 1206.32


    Number of generations: 100
Time taken to run 1000 algorithms: 15.68 seconds
Number of perfect solutions found: 992/1000 - 99.20%
Average perfect solution found at generation: 57.58/100
Average fitness evaluations: 1199.30


    Number of generations: 50
Time taken to run 1000 algorithms: 13.21 seconds
Number of perfect solutions found: 255/1000 - 25.50%
Average perfect solution found at generation: 44.48/50
Average fitness evaluations: 997.94

Finished all algorithms


#### Results:
The results for the number of generations are similar to population size. 2 different distinctions that can be made here:<br>

__The higher the number of generations:__
- it takes longer to run
- it is more likely to find a perfect solution<br><br>

__The lowest the number of generations:__
- it is quicker
- it is less likely to find a perfect solution

There is only a slight difference in the number of fitness evaluations made and the average number of generations needed to find the perfect solution over the mid-to-high range.
<br>

With these results, selecting the best number of generations depends on the problem. More generations should be selected if the problem requires a high return on perfect solutions. On the other hand, if speed is important, fewer generations should be selected; however, this will likely result in a lower chance of finding the perfect solution. Compared to population size, the number of generations generally does not affect the number of generations taken to find the perfect solution. The best number of generations is around 100; any lower will start not producing perfect solutions.

#### Analysing the crossover rate:

In [9]:
print("Starting algorithms")
crossoverRate = 1
print("\n    Crossover rate:", crossoverRate)
runAlgorithm()

crossoverRate = 0.5
print("\n    Crossover rate:", crossoverRate)
runAlgorithm()

crossoverRate = 0
print("\n    Crossover rate:", crossoverRate)
runAlgorithm()
print("Finished all algorithms")

Starting algorithms

    Crossover rate: 1
Time taken to run 1000 algorithms: 15.35 seconds
Number of perfect solutions found: 997/1000 - 99.70%
Average perfect solution found at generation: 53.84/100
Average fitness evaluations: 1120.42


    Crossover rate: 0.5
Time taken to run 1000 algorithms: 16.32 seconds
Number of perfect solutions found: 981/1000 - 98.10%
Average perfect solution found at generation: 61.16/100
Average fitness evaluations: 1278.54


    Crossover rate: 0
Time taken to run 1000 algorithms: 18.79 seconds
Number of perfect solutions found: 884/1000 - 88.40%
Average perfect solution found at generation: 76.26/100
Average fitness evaluations: 1618.94

Finished all algorithms


#### Results:
The results of the crossover rate show a slight difference.<br>

__The higher the crossover rate:__
- it takes fractionally less time to run
- it finds the perfect solution with less generations
- actions less fitness evaluations
- it finds the perfect solution more often<br><br>

__The lowest the crossover rate:__
- it takes fractionally more time to run
- it takes more generations to find the perfect solution
- processes more fitness evaluations
- reduces the number of perfect solutions found

Since the higher crossover rate results in finding the perfect solution faster and breaking out earlier, fewer fitness evaluations are performed. Not having any crossovers (crossover rate set to 0) does result in a high number of perfect solutions found ~90%; however, using 0.5 or more crossover rate increases that to around ~98+%, which shows that the crossover rate does provide a benefit to the GA. As for the best crossover rate, a crossover rate of 1 is the most effective.

#### Analysing the mutation rate:

In [10]:
print("Starting algorithms")
mutationRate = 0.025
print("\n    Mutation rate:", mutationRate)
runAlgorithm()

mutationRate = 0.02
print("\n    Mutation rate:", mutationRate)
runAlgorithm()

mutationRate = 0.01
print("\n    Mutation rate:", mutationRate)
runAlgorithm()

mutationRate = 0.005
print("\n    Mutation rate:", mutationRate)
runAlgorithm()
print("Finished all algorithms")

Starting algorithms

    Mutation rate: 0.025
Time taken to run 1000 algorithms: 18.77 seconds
Number of perfect solutions found: 962/1000 - 96.20%
Average perfect solution found at generation: 67.00/100
Average fitness evaluations: 1405.32


    Mutation rate: 0.02
Time taken to run 1000 algorithms: 16.63 seconds
Number of perfect solutions found: 977/1000 - 97.70%
Average perfect solution found at generation: 60.29/100
Average fitness evaluations: 1264.60


    Mutation rate: 0.01
Time taken to run 1000 algorithms: 15.69 seconds
Number of perfect solutions found: 987/1000 - 98.70%
Average perfect solution found at generation: 57.07/100
Average fitness evaluations: 1193.24


    Mutation rate: 0.005
Time taken to run 1000 algorithms: 18.89 seconds
Number of perfect solutions found: 915/1000 - 91.50%
Average perfect solution found at generation: 68.75/100
Average fitness evaluations: 1467.34

Finished all algorithms


#### Results:
The results for the mutation rate are not the case of higher versus lower values, as there is a middle ground between 0.01-0.02; however, any higher or lower than that range results in less perfect solutions found, longer time taken, and a higher number of generations to find the perfect solution. If the mutation rate is too high, then the GA is essentially random and is unlikely to find the perfect solution; on the other hand, if the mutation rate is too low, it can result in stagnation which is also unlikely to find the perfect solution, so mutation rate is a crucial hyper-parameter to get right.<br>
Nevertheless, a mutation rate between 0.01 and 0.02 is the most effective.

#### Analysing the tournament selection size:

In [11]:
print("Starting algorithms")
numberOfTournament = 8
print("\n    Number of individuals selected for tournament selection:", numberOfTournament)
runAlgorithm()

numberOfTournament = 4
print("\n    Number of individuals selected for tournament selection:", numberOfTournament)
runAlgorithm()

numberOfTournament = 2
print("\n    Number of individuals selected for tournament selection:", numberOfTournament)
runAlgorithm()
print("Finished all algorithms")

Starting algorithms

    Number of individuals selected for tournament selection: 8
Time taken to run 1000 algorithms: 15.37 seconds
Number of perfect solutions found: 999/1000 - 99.90%
Average perfect solution found at generation: 42.47/100
Average fitness evaluations: 891.54


    Number of individuals selected for tournament selection: 4
Time taken to run 1000 algorithms: 14.51 seconds
Number of perfect solutions found: 990/1000 - 99.00%
Average perfect solution found at generation: 47.64/100
Average fitness evaluations: 1004.04


    Number of individuals selected for tournament selection: 2
Time taken to run 1000 algorithms: 15.72 seconds
Number of perfect solutions found: 986/1000 - 98.60%
Average perfect solution found at generation: 57.49/100
Average fitness evaluations: 1202.36

Finished all algorithms


#### Results:
The results for the tournament selection size show that increasing.<br>

__The higher the tournament selection size:__
- it finds the perfect solution with less generations
- performs less fitness evaluations<br><br>

__The lowest the tournament selection size:__
- it takes more generations to find the perfect solution
- performs more fitness evaluations

The results show that the higher the number of individials selected for the tournament selection, the faster it will find the perfect solution, this also means that there are less evaluations performed. However, this does not follow with the time taken since the more individuals in the tournament, the more calcuations are required to get the best chromosome which offsets the fact that they normally breakout earlier. Conversely, with the minimum selection size, it takes longer to breakout which increases the fitness evaluations performed as well as the time taken; with this taken into account it shows that 4 is a good value for the selection size.<br>

When using a tournament selection size closer to the population size, the more likely it is to select the best chromosome to crossover/mutate and result in a better chromosome than the worse in the population. This makes me think that, at least for this problem, always choosing the best chromosome may be more benefitial than using tournament selection.

#### Comparing the best hyper-parameter values with the default values:

In [12]:
print("Starting algorithms\n")

resetHyperParameters()
print("   Default ", end = "")
printHyperParameters()
print("    Results:")
runAlgorithm()



populationSize = 25
numberOfGenerations = 100
crossoverRate = 1
mutationRate = 0.015
numberOfTournament = 4

print("\n\n   Best ", end = "")
printHyperParameters()
print("    Results:")
runAlgorithm()

print("Finished all algorithms")

Starting algorithms

   Default Hyper-parameters:
Population size: 20
Number of generations: 100
Number of individuals in tournament selection: 2
Crossover rate: 0.7
Mutation rate (per bit): 0.01 

    Results:
Time taken to run 1000 algorithms: 16.09 seconds
Number of perfect solutions found: 987/1000 - 98.70%
Average perfect solution found at generation: 57.94/100
Average fitness evaluations: 1210.54



   Best Hyper-parameters:
Population size: 25
Number of generations: 100
Number of individuals in tournament selection: 4
Crossover rate: 1
Mutation rate (per bit): 0.015 

    Results:
Time taken to run 1000 algorithms: 15.05 seconds
Number of perfect solutions found: 1000/1000 - 100.00%
Average perfect solution found at generation: 36.57/100
Average fitness evaluations: 965.20

Finished all algorithms


#### Results:

__Best hyper-parameters compared to default hyper-parameters:__
- Executes faster (~4% faster)
- More perfect solutions found (~1.5% more)
- Finds the perfect solution sooner (~36% faster)
- Less fitness evaluations (~20% less)

These results show a definite improvement compared to the initial default parameters. One interesting finding is the number of generations taken to find the perfect solution; it shows that, on average, it finds the perfect solution at around the 36th generation, which is small compared to the 100 possible generations. However, if the number of generations is reduced, then the number of perfect solutions starts to decline. From the previous analysis, I believe this indicates that sometimes the GA stagnates.<br>
An idea I have had is to use a neural network to use the hyper-parameters as nodes, which with a chosen weight, may find the most influential parameters for that weight, e.g. if the problem requires speed/accuracy or a balance.

## 3. Fitness function

The observations and discussions are found after all function minimum/maximums.

#### Method to run GA for fitness function section:

__*runGAWithResultsOutput(minimisedFunction)*__<br>
Runs the GA with the updated fitness function and displays the results.

In [13]:
#Variables to decode chromosomes
numberOfBitsPerNumber = 50
numberOfNumbers = 2
numberOfBits = numberOfBitsPerNumber * numberOfNumbers
padding = 100000


def runGAWithResultsOutput(minimisedFunction):
    """Runs the GA with the updated fitness function and displays the results.
    
    minimisedFunction: boolean for determining if the caller is minimising the function or not."""
    
    startTime = timeit.default_timer()
    run = runGA(displayASCII = False)
    timeElapsed = timeit.default_timer() - startTime

    print("Results:")
    print("Time taken: {:.2f} seconds".format(timeElapsed))
    print("Fitness evaluations:", run[2])
    print("Best solution found at generation: {}/{}".format(run[0], numberOfGenerations))
    print("Best chromosome:", run[3])
    
    score = fitness(run[3])
    
    if minimisedFunction:
        #Removing the extra padding from the final result
        score = score - padding
    
    print("\nBest fitness score:", score)
    print("x:", decodeChromosome(run[3])[0])
    print("y:", decodeChromosome(run[3])[1])

#### Single-objective optimisation function: Ackley function
##### Ackley function - Minimum:
Contains overwritten methods for fitness() and decodeChromosome(). It also contains a new method __*decodeRealValue()*__ which uses fixed-point representation to represent real numbers and scales the number into the range minValue-maxValue.

In [14]:
def fitness(chromosome):
    """Evaluates the fitness score of a chromosome, which is the 'padding' - Ackley function, this
    results in minimising the function."""
    
    global fitnessEvaluationCount
    fitnessEvaluationCount += 1
    
    x, y = decodeChromosome(chromosome)
    
    score = -20 * math.exp(-0.2 * math.sqrt(0.5*(x*x + y*y))) - math.exp(0.5*(math.cos(2 * math.pi * x) + math.cos(2 * math.pi * y))) + math.exp(1) + 20
    
    return padding - score

def decodeRealValue(binaryString, minValue, maxValue):
    """Using fixed-point representation of real numbers and using int(number, base) to
    convert fromn binary (base 2) to a decimal, scaling with a min and max value."""
    
    decimal = int(binaryString, 2)
    
    return minValue + (decimal / (2**numberOfBitsPerNumber - 1)) * (maxValue - minValue)


def decodeChromosome(chromosome):
    """Returns the x and y decimal values of the chromosome."""

    x_binary = chromosome[:numberOfBitsPerNumber]
    y_binary = chromosome[numberOfBitsPerNumber:]

    x = decodeRealValue(x_binary, -5, 5)
    y = decodeRealValue(y_binary, -5, 5)

    return x, y


populationSize = 40
numberOfGenerations = 200
crossoverRate = 1
mutationRate = 0.02
numberOfTournament = 4
runGAWithResultsOutput(minimisedFunction = True)

Start of GA

Hyper-parameters:
Population size: 40
Number of generations: 200
Number of individuals in tournament selection: 4
Crossover rate: 1
Mutation rate (per bit): 0.02 

Generation-0        Average fitness: 99994.54742300825       Best fitness: 99996.24551958167   
Generation-1        Average fitness: 99996.06206007612       Best fitness: 99996.37433929874   
Generation-2        Average fitness: 99996.30863602877       Best fitness: 99996.40107522033   
Generation-3        Average fitness: 99996.38521953137       Best fitness: 99996.40119054058   
Generation-4        Average fitness: 99996.39983404947       Best fitness: 99996.40141310994   
Generation-5        Average fitness: 99996.40139053047       Best fitness: 99996.40187335377   
Generation-6        Average fitness: 99996.40180458006       Best fitness: 99996.4018902994    
Generation-7        Average fitness: 99996.40188047793       Best fitness: 99996.40190370887   
Generation-8        Average fitness: 99996.40189257104 

Generation-98       Average fitness: 100000.0                Best fitness: 100000.0            
Generation-99       Average fitness: 99999.99998919491       Best fitness: 100000.0            
Generation-100      Average fitness: 99999.99995657199       Best fitness: 100000.0            
Generation-101      Average fitness: 99999.80813720495       Best fitness: 100000.0            
Generation-102      Average fitness: 100000.0                Best fitness: 100000.0            
Generation-103      Average fitness: 99999.9961603995        Best fitness: 100000.0            
Generation-104      Average fitness: 99999.9999998314        Best fitness: 100000.0            
Generation-105      Average fitness: 99999.99999999996       Best fitness: 100000.0            
Generation-106      Average fitness: 99999.99999865107       Best fitness: 100000.0            
Generation-107      Average fitness: 99999.98979409046       Best fitness: 100000.0            
Generation-108      Average fitness: 999

##### Ackley function - Maximum:
Contains overwritten methods for fitness() and decodeChromosome().

In [15]:
def decodeChromosome(chromosome):
    """Returns the x and y decimal values of the chromosome."""

    x_binary = chromosome[:numberOfBitsPerNumber]
    y_binary = chromosome[numberOfBitsPerNumber:]

    x = decodeRealValue(x_binary, -5, 5)
    y = decodeRealValue(y_binary, -5, 5)

    return x, y

def fitness(chromosome):
    """Evaluates the fitness score of a chromosome, which is the maximum of the Ackley function."""
    
    global fitnessEvaluationCount
    fitnessEvaluationCount += 1
    
    x, y = decodeChromosome(chromosome)
    
    score = -20 * math.exp(-0.2 * math.sqrt(0.5*(x*x + y*y))) - math.exp(0.5*(math.cos(2 * math.pi * x) + math.cos(2 * math.pi * y))) + math.exp(1) + 20
    
    return score


populationSize = 40
numberOfGenerations = 5000
crossoverRate = 1
mutationRate = 0.02
numberOfTournament = 4
runGAWithResultsOutput(minimisedFunction = False)

Start of GA

Hyper-parameters:
Population size: 40
Number of generations: 5000
Number of individuals in tournament selection: 4
Crossover rate: 1
Mutation rate (per bit): 0.02 

Generation-0        Average fitness: 13.343980490943144      Best fitness: 14.266647406683646  
Generation-1        Average fitness: 14.237463296054873      Best fitness: 14.27032006978992   
Generation-2        Average fitness: 14.27010939647965       Best fitness: 14.282650899534977  
Generation-3        Average fitness: 14.276005524611929      Best fitness: 14.28358519558853   
Generation-4        Average fitness: 14.283281551546215      Best fitness: 14.283724767185188  
Generation-5        Average fitness: 14.283635930966193      Best fitness: 14.284290985743654  
Generation-6        Average fitness: 14.283806764603483      Best fitness: 14.284624128010151  
Generation-7        Average fitness: 14.284215268521498      Best fitness: 14.284624173151284  
Generation-8        Average fitness: 14.28460851268609

Generation-155      Average fitness: 14.270824568897893      Best fitness: 14.302666944783399  
Generation-156      Average fitness: 14.302666944783383      Best fitness: 14.302666944783399  
Generation-157      Average fitness: 14.302666944783407      Best fitness: 14.302666944783399  
Generation-158      Average fitness: 14.302624969080728      Best fitness: 14.302666944783399  
Generation-159      Average fitness: 14.302656702441917      Best fitness: 14.302666944783399  
Generation-160      Average fitness: 14.243355390600092      Best fitness: 14.302666944783399  
Generation-161      Average fitness: 14.302666491174168      Best fitness: 14.302666944783399  
Generation-162      Average fitness: 14.302666944783407      Best fitness: 14.302666944783399  
Generation-163      Average fitness: 14.3026669447834        Best fitness: 14.302666944783399  
Generation-164      Average fitness: 14.302666944757192      Best fitness: 14.302666944783399  
Generation-165      Average fitness: 14.

Generation-431      Average fitness: 14.302666944760869      Best fitness: 14.302666944783399  
Generation-432      Average fitness: 14.302666944783406      Best fitness: 14.302666944783399  
Generation-433      Average fitness: 14.302666944783406      Best fitness: 14.302666944783399  
Generation-434      Average fitness: 14.302666944783407      Best fitness: 14.302666944783399  
Generation-435      Average fitness: 14.273631827090181      Best fitness: 14.302666944783399  
Generation-436      Average fitness: 14.300171372986762      Best fitness: 14.302666944783399  
Generation-437      Average fitness: 14.241688094263798      Best fitness: 14.302666944783399  
Generation-438      Average fitness: 14.241691406346025      Best fitness: 14.302666944783399  
Generation-439      Average fitness: 14.302666693190755      Best fitness: 14.302666944783399  
Generation-440      Average fitness: 14.302666944783407      Best fitness: 14.302666944783399  
Generation-441      Average fitness: 14.

Generation-674      Average fitness: 14.302666944783358      Best fitness: 14.302666944783399  
Generation-675      Average fitness: 14.302666944781212      Best fitness: 14.302666944783399  
Generation-676      Average fitness: 14.302503186785035      Best fitness: 14.302666944783399  
Generation-677      Average fitness: 14.241709141049801      Best fitness: 14.302666944783399  
Generation-678      Average fitness: 14.302656699936488      Best fitness: 14.302666944783399  
Generation-679      Average fitness: 14.302666944783406      Best fitness: 14.302666944783399  
Generation-680      Average fitness: 14.302666944760869      Best fitness: 14.302666944783399  
Generation-681      Average fitness: 14.30266694478332       Best fitness: 14.302666944783399  
Generation-682      Average fitness: 14.241691546960501      Best fitness: 14.302666944783399  
Generation-683      Average fitness: 14.294606251412691      Best fitness: 14.302666944783399  
Generation-684      Average fitness: 14.

Generation-890      Average fitness: 14.274142035636425      Best fitness: 14.302666944783399  
Generation-891      Average fitness: 14.243362179049132      Best fitness: 14.302666944783399  
Generation-892      Average fitness: 14.274155729707962      Best fitness: 14.302666944783399  
Generation-893      Average fitness: 14.294581610246166      Best fitness: 14.302666944783399  
Generation-894      Average fitness: 14.302666944783407      Best fitness: 14.302666944783399  
Generation-895      Average fitness: 14.276877107979521      Best fitness: 14.302666944783399  
Generation-896      Average fitness: 14.302666944781214      Best fitness: 14.302666944783399  
Generation-897      Average fitness: 14.302666900011507      Best fitness: 14.302666944783399  
Generation-898      Average fitness: 14.302666941744146      Best fitness: 14.302666944783399  
Generation-899      Average fitness: 14.294625243402038      Best fitness: 14.302666944783399  
Generation-900      Average fitness: 14.

...

Generation-3832     Average fitness: 14.302667457654039      Best fitness: 14.302667499374492  
Generation-3833     Average fitness: 14.302667499374483      Best fitness: 14.302667499374492  
Generation-3834     Average fitness: 14.302667499374333      Best fitness: 14.302667499374492  
Generation-3835     Average fitness: 14.271228553751607      Best fitness: 14.302667499374492  
Generation-3836     Average fitness: 14.302667499374483      Best fitness: 14.302667499374492  
Generation-3837     Average fitness: 14.302667499373865      Best fitness: 14.302667499374492  
Generation-3838     Average fitness: 14.302667499374257      Best fitness: 14.302667499374492  
Generation-3839     Average fitness: 14.27386250944673       Best fitness: 14.302667499374492  
Generation-3840     Average fitness: 14.30266686221365       Best fitness: 14.302667499374492  
Generation-3841     Average fitness: 14.302506703075775      Best fitness: 14.302667499374492  
Generation-3842     Average fitness: 14.

Generation-4091     Average fitness: 14.302667499277707      Best fitness: 14.302667499374492  
Generation-4092     Average fitness: 14.277948118186746      Best fitness: 14.302667499374492  
Generation-4093     Average fitness: 14.302667499103075      Best fitness: 14.302667499374492  
Generation-4094     Average fitness: 14.302666870530254      Best fitness: 14.302667499374492  
Generation-4095     Average fitness: 14.302667496421197      Best fitness: 14.302667499374492  
Generation-4096     Average fitness: 14.302627761401634      Best fitness: 14.302667499374492  
Generation-4097     Average fitness: 14.294711474058104      Best fitness: 14.302667499374492  
Generation-4098     Average fitness: 14.302667499374483      Best fitness: 14.302667499374492  
Generation-4099     Average fitness: 14.301998251348811      Best fitness: 14.302667499374492  
Generation-4100     Average fitness: 14.302667457654039      Best fitness: 14.302667499374492  
Generation-4101     Average fitness: 14.

Generation-4296     Average fitness: 14.302667496882473      Best fitness: 14.302667499374492  
Generation-4297     Average fitness: 14.243381935946752      Best fitness: 14.302667499374492  
Generation-4298     Average fitness: 14.302667499374483      Best fitness: 14.302667499374492  
Generation-4299     Average fitness: 14.302667499374483      Best fitness: 14.302667499374492  
Generation-4300     Average fitness: 14.302667499374483      Best fitness: 14.302667499374492  
Generation-4301     Average fitness: 14.302667499374483      Best fitness: 14.302667499374492  
Generation-4302     Average fitness: 14.300170758673769      Best fitness: 14.302667499374492  
Generation-4303     Average fitness: 14.302667499374483      Best fitness: 14.302667499374492  
Generation-4304     Average fitness: 14.30198786763962       Best fitness: 14.302667499374492  
Generation-4305     Average fitness: 14.302667339853937      Best fitness: 14.302667499374492  
Generation-4306     Average fitness: 14.

Generation-4508     Average fitness: 14.302657257312442      Best fitness: 14.302667499374492  
Generation-4509     Average fitness: 14.302667499372001      Best fitness: 14.302667499374492  
Generation-4510     Average fitness: 14.302667499357588      Best fitness: 14.302667499374492  
Generation-4511     Average fitness: 14.302667499374483      Best fitness: 14.302667499374492  
Generation-4512     Average fitness: 14.302667498983094      Best fitness: 14.302667499374492  
Generation-4513     Average fitness: 14.295036551886074      Best fitness: 14.302667499374492  
Generation-4514     Average fitness: 14.302667499374483      Best fitness: 14.302667499374492  
Generation-4515     Average fitness: 14.30017075871493       Best fitness: 14.302667499374492  
Generation-4516     Average fitness: 14.300189545162482      Best fitness: 14.302667499374492  
Generation-4517     Average fitness: 14.30266174348514       Best fitness: 14.302667499374492  
Generation-4518     Average fitness: 14.

Generation-4802     Average fitness: 14.302667499366654      Best fitness: 14.302667499374492  
Generation-4803     Average fitness: 14.266580899673695      Best fitness: 14.302667499374492  
Generation-4804     Average fitness: 14.302667496882375      Best fitness: 14.302667499374492  
Generation-4805     Average fitness: 14.302667459502448      Best fitness: 14.302667499374492  
Generation-4806     Average fitness: 14.300170724876413      Best fitness: 14.302667499374492  
Generation-4807     Average fitness: 14.302667339853977      Best fitness: 14.302667499374492  
Generation-4808     Average fitness: 14.302667457654039      Best fitness: 14.302667499374492  
Generation-4809     Average fitness: 14.302666862212437      Best fitness: 14.302667499374492  
Generation-4810     Average fitness: 14.24170087865284       Best fitness: 14.302667499374492  
Generation-4811     Average fitness: 14.302667499366644      Best fitness: 14.302667499374492  
Generation-4812     Average fitness: 14.

#### Constrainged optimisation function: Rosenbrock function constrained with a cubic and a line
##### Rosenbrock function constrained - Minimum:
Contains overwritten methods for fitness() and decodeChromosome().

In [16]:
def fitness(chromosome):
    """Evaluates the fitness score of a chromosome, which is the 'padding' - Rosenbrock function, this
    results in minimising the function.
    This function is contrains x and y values with a cubic and a line returning 1 to penalise 
    that chromosome."""
    
    global fitnessEvaluationCount
    fitnessEvaluationCount += 1
    
    x, y = decodeChromosome(chromosome)
    
    
    if (x - 1)**3 - y > 0 or x + y - 2 > 0:
        return 1
    
    score = (1 - x)**2 + 100*(y - x*x)**2
    
    return padding - score


def decodeChromosome(chromosome):
    """Returns the x and y decimal values of the chromosome"""

    x_binary = chromosome[:numberOfBitsPerNumber]
    y_binary = chromosome[numberOfBitsPerNumber:]

    x = decodeRealValue(x_binary, -1.5, 1.5)
    y = decodeRealValue(y_binary, -0.5, 2.5)

    return x, y


populationSize = 40
numberOfGenerations = 4000
crossoverRate = 1
mutationRate = 0.2
numberOfTournament = 4
runGAWithResultsOutput(minimisedFunction = True)

Start of GA

Hyper-parameters:
Population size: 40
Number of generations: 4000
Number of individuals in tournament selection: 4
Crossover rate: 1
Mutation rate (per bit): 0.2 

Generation-0        Average fitness: 99972.75251160351       Best fitness: 99998.62887475248   
Generation-1        Average fitness: 99990.66478784337       Best fitness: 99998.62887475248   
Generation-2        Average fitness: 99995.44971389309       Best fitness: 99998.62887475248   
Generation-3        Average fitness: 99997.04963507374       Best fitness: 99998.62887475248   
Generation-4        Average fitness: 99996.16654709613       Best fitness: 99998.77406629852   
Generation-5        Average fitness: 99997.19252925723       Best fitness: 99998.77406629852   
Generation-6        Average fitness: 99998.46547471969       Best fitness: 99998.87917419967   
Generation-7        Average fitness: 99995.36165514405       Best fitness: 99998.87917419967   
Generation-8        Average fitness: 99998.57353362754 

Generation-87       Average fitness: 97499.98462298836       Best fitness: 99999.99487178645   
Generation-88       Average fitness: 97499.98620805974       Best fitness: 99999.99487178645   
Generation-89       Average fitness: 99999.54662615758       Best fitness: 99999.99510928981   
Generation-90       Average fitness: 99997.86373033885       Best fitness: 99999.99510928981   
Generation-91       Average fitness: 97499.99356591245       Best fitness: 99999.99516429746   
Generation-92       Average fitness: 97499.99356591245       Best fitness: 99999.99516429746   
Generation-93       Average fitness: 99998.54446545479       Best fitness: 99999.99516429746   
Generation-94       Average fitness: 97499.99673744792       Best fitness: 99999.99516429746   
Generation-95       Average fitness: 99998.21785687664       Best fitness: 99999.99516429746   
Generation-96       Average fitness: 99990.10872911951       Best fitness: 99999.99516429746   
Generation-97       Average fitness: 975

Generation-377      Average fitness: 97500.02099348688       Best fitness: 99999.99609087738   
Generation-378      Average fitness: 99999.98129587565       Best fitness: 99999.99609087738   
Generation-379      Average fitness: 99999.98517143875       Best fitness: 99999.99609087738   
Generation-380      Average fitness: 99999.88825319581       Best fitness: 99999.99609087738   
Generation-381      Average fitness: 99998.18636691906       Best fitness: 99999.99609087738   
Generation-382      Average fitness: 97500.02099348688       Best fitness: 99999.99609087738   
Generation-383      Average fitness: 99999.03322546111       Best fitness: 99999.99609087738   
Generation-384      Average fitness: 99999.58438400886       Best fitness: 99999.99609087738   
Generation-385      Average fitness: 99999.99589953994       Best fitness: 99999.99609087738   
Generation-386      Average fitness: 99998.78370111447       Best fitness: 99999.99609087738   
Generation-387      Average fitness: 975

Generation-609      Average fitness: 97500.02114450553       Best fitness: 99999.99609087738   
Generation-610      Average fitness: 99998.6069814407        Best fitness: 99999.99609087738   
Generation-611      Average fitness: 99999.9877457789        Best fitness: 99999.99609087738   
Generation-612      Average fitness: 99992.18440249404       Best fitness: 99999.99609087738   
Generation-613      Average fitness: 99998.82367012078       Best fitness: 99999.99609087738   
Generation-614      Average fitness: 99997.58871840805       Best fitness: 99999.99609087738   
Generation-615      Average fitness: 97500.02114528246       Best fitness: 99999.99609087738   
Generation-616      Average fitness: 99995.65745729534       Best fitness: 99999.99609087738   
Generation-617      Average fitness: 99999.99542705344       Best fitness: 99999.99609087738   
Generation-618      Average fitness: 99990.41132212782       Best fitness: 99999.99609087738   
Generation-619      Average fitness: 999

Generation-710      Average fitness: 99998.93802776188       Best fitness: 99999.99609088544   
Generation-711      Average fitness: 99999.42489387614       Best fitness: 99999.99609088544   
Generation-712      Average fitness: 99998.06119980168       Best fitness: 99999.99609088544   
Generation-713      Average fitness: 97500.0211618256        Best fitness: 99999.99609088544   
Generation-714      Average fitness: 99996.25016098516       Best fitness: 99999.99609088544   
Generation-715      Average fitness: 97500.021162304         Best fitness: 99999.99609088544   
Generation-716      Average fitness: 99999.18933641023       Best fitness: 99999.99609088544   
Generation-717      Average fitness: 99998.89719041431       Best fitness: 99999.99609088544   
Generation-718      Average fitness: 99999.23246986134       Best fitness: 99999.99609088544   
Generation-719      Average fitness: 99999.98866015297       Best fitness: 99999.99609088544   
Generation-720      Average fitness: 999

...

Generation-3259     Average fitness: 97500.02498498547       Best fitness: 99999.99998469677   
Generation-3260     Average fitness: 99999.95971895616       Best fitness: 99999.99998469677   
Generation-3261     Average fitness: 99999.99331442112       Best fitness: 99999.99998469677   
Generation-3262     Average fitness: 99997.79896830147       Best fitness: 99999.99998469677   
Generation-3263     Average fitness: 97500.02498498547       Best fitness: 99999.99998469677   
Generation-3264     Average fitness: 99999.91137069209       Best fitness: 99999.99998469677   
Generation-3265     Average fitness: 99999.91129087468       Best fitness: 99999.99998471135   
Generation-3266     Average fitness: 99999.96027131991       Best fitness: 99999.99998471135   
Generation-3267     Average fitness: 99999.86679700731       Best fitness: 99999.99998471135   
Generation-3268     Average fitness: 99998.75472131837       Best fitness: 99999.99998471135   
Generation-3269     Average fitness: 999

Generation-3395     Average fitness: 99999.40936363996       Best fitness: 99999.99998471135   
Generation-3396     Average fitness: 97500.0249849908        Best fitness: 99999.99998471135   
Generation-3397     Average fitness: 97500.0249849908        Best fitness: 99999.99998471135   
Generation-3398     Average fitness: 99999.18973990458       Best fitness: 99999.99998471135   
Generation-3399     Average fitness: 97500.0249849908        Best fitness: 99999.99998471135   
Generation-3400     Average fitness: 97500.0249849908        Best fitness: 99999.99998471135   
Generation-3401     Average fitness: 97500.0249849908        Best fitness: 99999.99998471135   
Generation-3402     Average fitness: 99999.8877846092        Best fitness: 99999.99998471135   
Generation-3403     Average fitness: 99991.42386874593       Best fitness: 99999.99998471135   
Generation-3404     Average fitness: 99992.50764519369       Best fitness: 99999.99998471135   
Generation-3405     Average fitness: 975

Generation-3498     Average fitness: 99999.96758280272       Best fitness: 99999.99998471135   
Generation-3499     Average fitness: 99999.62608633234       Best fitness: 99999.99998471135   
Generation-3500     Average fitness: 99999.70242151203       Best fitness: 99999.99998471135   
Generation-3501     Average fitness: 97500.02498500288       Best fitness: 99999.99998471135   
Generation-3502     Average fitness: 99998.84331638523       Best fitness: 99999.99998471135   
Generation-3503     Average fitness: 97500.02498500288       Best fitness: 99999.99998471135   
Generation-3504     Average fitness: 99997.02889532216       Best fitness: 99999.99998471135   
Generation-3505     Average fitness: 99990.85595519961       Best fitness: 99999.99998471135   
Generation-3506     Average fitness: 99999.99996749694       Best fitness: 99999.99998471135   
Generation-3507     Average fitness: 97500.02498500288       Best fitness: 99999.99998471135   
Generation-3508     Average fitness: 975

Generation-3712     Average fitness: 99999.9905248397        Best fitness: 99999.99998471783   
Generation-3713     Average fitness: 99999.99998460554       Best fitness: 99999.99998471783   
Generation-3714     Average fitness: 97500.02498502129       Best fitness: 99999.99998471783   
Generation-3715     Average fitness: 99999.99996707922       Best fitness: 99999.99998471783   
Generation-3716     Average fitness: 99997.82140895787       Best fitness: 99999.99998471783   
Generation-3717     Average fitness: 97500.02498502129       Best fitness: 99999.99998471783   
Generation-3718     Average fitness: 97500.02498502129       Best fitness: 99999.99998471783   
Generation-3719     Average fitness: 99998.66775029864       Best fitness: 99999.99998471783   
Generation-3720     Average fitness: 99999.98137768234       Best fitness: 99999.99998471783   
Generation-3721     Average fitness: 99998.7892776994        Best fitness: 99999.99998471783   
Generation-3722     Average fitness: 975

Generation-3999     Average fitness: 99999.97911911311       Best fitness: 99999.99998473912   


Solutions sampled: 160,000
Search space: 1,267,650,600,228,229,401,496,703,205,376
Fraction of search space explored: 1.262177448353619e-25%
Number of fitness evaluations: 160040

Best chromosome: 99999.99998473912
Reached at generation 3968
Output:
1101010011111111111111101111000111100101001111110001111111010101011001101010010011000000001111101111

End of GA
Results:
Time taken: 2.44 seconds
Fitness evaluations: 160042
Best solution found at generation: 3968/4000
Best chromosome: 1101010011111111111111101111000111100101001111110001111111010101011001101010010011000000001111101111

Best fitness score: -1.5260884538292885e-05
x: 0.9960935613341833
y: 0.9921998812378221


##### Rosenbrock function constrained - Maximum:
Contains overwritten methods for fitness() and decodeChromosome().

In [17]:
def fitness(chromosome):
    """Evaluates the fitness score of a chromosome, which is the maximum of the Rosenbrock function.
    This function is contrains x and y values with a cubic and a line returning 1 to penalise 
    that chromosome."""
    
    global fitnessEvaluationCount
    fitnessEvaluationCount += 1
    
    x, y = decodeChromosome(chromosome)
    
    
    if (x - 1)**3 - y > 0 or x + y - 2 > 0:
        return 1
    
    score = (1 - x)**2 + 100*(y - x*x)**2
    
    return score


def decodeChromosome(chromosome):
    """Returns the x and y decimal values of the chromosome"""

    x_binary = chromosome[:numberOfBitsPerNumber]
    y_binary = chromosome[numberOfBitsPerNumber:]

    x = decodeRealValue(x_binary, -1.5, 1.5)
    y = decodeRealValue(y_binary, -0.5, 2.5)

    return x, y


populationSize = 40
numberOfGenerations = 4000
crossoverRate = 1
mutationRate = 0.1
numberOfTournament = 4
runGAWithResultsOutput(minimisedFunction = False)

Start of GA

Hyper-parameters:
Population size: 40
Number of generations: 4000
Number of individuals in tournament selection: 4
Crossover rate: 1
Mutation rate (per bit): 0.1 

Generation-0        Average fitness: 226.9731976133083       Best fitness: 386.7110585683655   
Generation-1        Average fitness: 286.8287415587727       Best fitness: 452.57488091259154  
Generation-2        Average fitness: 350.9227573189704       Best fitness: 468.3285714612216   
Generation-3        Average fitness: 433.9397339485151       Best fitness: 469.7147853336862   
Generation-4        Average fitness: 457.3197657545259       Best fitness: 469.8363094003006   
Generation-5        Average fitness: 454.6892766095194       Best fitness: 471.09698896125207  
Generation-6        Average fitness: 457.7718650131622       Best fitness: 499.29839597352833  
Generation-7        Average fitness: 471.0026277506966       Best fitness: 499.29839597352833  
Generation-8        Average fitness: 463.9127514902766 

Generation-285      Average fitness: 508.3363106290969       Best fitness: 508.4996838698039   
Generation-286      Average fitness: 497.9518140195294       Best fitness: 508.4996838698039   
Generation-287      Average fitness: 507.4580295595323       Best fitness: 508.4996838698039   
Generation-288      Average fitness: 495.8111874920099       Best fitness: 508.4996838698039   
Generation-289      Average fitness: 506.4696887794697       Best fitness: 508.4996838698039   
Generation-290      Average fitness: 498.0760116469669       Best fitness: 508.4996838698039   
Generation-291      Average fitness: 495.8111874920099       Best fitness: 508.4996838698039   
Generation-292      Average fitness: 505.9654213182395       Best fitness: 508.4996838698039   
Generation-293      Average fitness: 505.7125300136793       Best fitness: 508.4996838698039   
Generation-294      Average fitness: 508.4573982870177       Best fitness: 508.4996838698039   
Generation-295      Average fitness: 507

Generation-662      Average fitness: 495.81238086248175      Best fitness: 508.4999608811169   
Generation-663      Average fitness: 496.00174044699344      Best fitness: 508.4999608811169   
Generation-664      Average fitness: 508.4001171358094       Best fitness: 508.4999608811169   
Generation-665      Average fitness: 506.22948679780393      Best fitness: 508.4999608811169   
Generation-666      Average fitness: 508.4649362170082       Best fitness: 508.4999608811169   
Generation-667      Average fitness: 496.1388031274158       Best fitness: 508.4999608811169   
Generation-668      Average fitness: 508.47403298387945      Best fitness: 508.4999608811169   
Generation-669      Average fitness: 495.8123818822734       Best fitness: 508.4999608811169   
Generation-670      Average fitness: 495.8123818822734       Best fitness: 508.4999608811169   
Generation-671      Average fitness: 495.8123818822734       Best fitness: 508.4999608811169   
Generation-672      Average fitness: 505

Generation-1015     Average fitness: 762.2108267802394       Best fitness: 762.4535558486973   
Generation-1016     Average fitness: 743.2950426166824       Best fitness: 762.4535558486973   
Generation-1017     Average fitness: 757.2625450628535       Best fitness: 762.4535558486973   
Generation-1018     Average fitness: 754.6547113543473       Best fitness: 762.4535558486973   
Generation-1019     Average fitness: 761.5874335153005       Best fitness: 762.4535558486973   
Generation-1020     Average fitness: 750.9440455137926       Best fitness: 762.4535558486973   
Generation-1021     Average fitness: 753.4056916988608       Best fitness: 762.4822570238077   
Generation-1022     Average fitness: 759.5522443559641       Best fitness: 762.4822570238077   
Generation-1023     Average fitness: 745.0608297484366       Best fitness: 762.4822570238077   
Generation-1024     Average fitness: 745.5694441524253       Best fitness: 762.4822570238077   
Generation-1025     Average fitness: 761

Generation-1445     Average fitness: 762.3669109677844       Best fitness: 762.4999712552659   
Generation-1446     Average fitness: 758.6071556775258       Best fitness: 762.4999712552659   
Generation-1447     Average fitness: 762.177279377588        Best fitness: 762.4999712552659   
Generation-1448     Average fitness: 750.2055231366137       Best fitness: 762.4999712552659   
Generation-1449     Average fitness: 760.5619185179542       Best fitness: 762.4999712552659   
Generation-1450     Average fitness: 746.1252136747639       Best fitness: 762.4999712552659   
Generation-1451     Average fitness: 747.2035611014094       Best fitness: 762.4999712552659   
Generation-1452     Average fitness: 753.5856287593668       Best fitness: 762.4999712552659   
Generation-1453     Average fitness: 753.5926827241427       Best fitness: 762.4999712552659   
Generation-1454     Average fitness: 758.0528388474293       Best fitness: 762.4999712552659   
Generation-1455     Average fitness: 761

...

Generation-3011     Average fitness: 746.9863084567831       Best fitness: 762.4999996464305   
Generation-3012     Average fitness: 757.9786585677767       Best fitness: 762.4999996464305   
Generation-3013     Average fitness: 762.4980509905129       Best fitness: 762.4999996464305   
Generation-3014     Average fitness: 747.4233457104267       Best fitness: 762.4999996464305   
Generation-3015     Average fitness: 762.4999754781876       Best fitness: 762.4999996464305   
Generation-3016     Average fitness: 758.5532720895906       Best fitness: 762.4999996464305   
Generation-3017     Average fitness: 744.0877250788564       Best fitness: 762.4999996464305   
Generation-3018     Average fitness: 762.493544387193        Best fitness: 762.4999996464305   
Generation-3019     Average fitness: 755.8593931898812       Best fitness: 762.4999996464305   
Generation-3020     Average fitness: 760.0094523357179       Best fitness: 762.4999996464305   
Generation-3021     Average fitness: 761

Generation-3406     Average fitness: 747.0728225447276       Best fitness: 762.4999998033929   
Generation-3407     Average fitness: 746.3090375378775       Best fitness: 762.4999998033929   
Generation-3408     Average fitness: 743.5482303263882       Best fitness: 762.4999998033929   
Generation-3409     Average fitness: 760.6380691514394       Best fitness: 762.4999998033929   
Generation-3410     Average fitness: 760.634442098787        Best fitness: 762.4999998033929   
Generation-3411     Average fitness: 747.4206820342777       Best fitness: 762.4999998033929   
Generation-3412     Average fitness: 743.6187463372712       Best fitness: 762.4999998033929   
Generation-3413     Average fitness: 762.4205569468724       Best fitness: 762.4999998033929   
Generation-3414     Average fitness: 747.4999723902145       Best fitness: 762.4999998033929   
Generation-3415     Average fitness: 750.884584629666        Best fitness: 762.4999998033929   
Generation-3416     Average fitness: 760

Generation-3536     Average fitness: 745.3626133528003       Best fitness: 762.4999998033929   
Generation-3537     Average fitness: 755.8547137041777       Best fitness: 762.4999998033929   
Generation-3538     Average fitness: 759.1091085417447       Best fitness: 762.4999998033929   
Generation-3539     Average fitness: 757.6949010301762       Best fitness: 762.4999998033929   
Generation-3540     Average fitness: 762.4543509555334       Best fitness: 762.4999998033929   
Generation-3541     Average fitness: 762.477910647403        Best fitness: 762.4999998033929   
Generation-3542     Average fitness: 762.476077389128        Best fitness: 762.4999998033929   
Generation-3543     Average fitness: 745.410922349781        Best fitness: 762.4999998033929   
Generation-3544     Average fitness: 753.9082376373219       Best fitness: 762.4999998033929   
Generation-3545     Average fitness: 760.0024108846417       Best fitness: 762.4999998033929   
Generation-3546     Average fitness: 762

Generation-3794     Average fitness: 744.0837287311148       Best fitness: 762.4999998893844   
Generation-3795     Average fitness: 762.4988047902381       Best fitness: 762.4999998893844   
Generation-3796     Average fitness: 762.4018333616416       Best fitness: 762.4999998893844   
Generation-3797     Average fitness: 753.417612028683        Best fitness: 762.4999998893844   
Generation-3798     Average fitness: 762.2390604397034       Best fitness: 762.4999998893844   
Generation-3799     Average fitness: 761.2216111631272       Best fitness: 762.4999998893844   
Generation-3800     Average fitness: 757.6901433932826       Best fitness: 762.4999998893844   
Generation-3801     Average fitness: 756.8840665280534       Best fitness: 762.4999998893844   
Generation-3802     Average fitness: 750.9352434188328       Best fitness: 762.4999998893844   
Generation-3803     Average fitness: 762.4042041848767       Best fitness: 762.4999998893844   
Generation-3804     Average fitness: 759

Generation-3975     Average fitness: 760.0251695977059       Best fitness: 762.4999999757736   
Generation-3976     Average fitness: 762.3577344913648       Best fitness: 762.4999999757736   
Generation-3977     Average fitness: 750.0127688188694       Best fitness: 762.4999999757736   
Generation-3978     Average fitness: 751.1970510287673       Best fitness: 762.4999999757736   
Generation-3979     Average fitness: 762.4968401120866       Best fitness: 762.4999999757736   
Generation-3980     Average fitness: 755.2496774902228       Best fitness: 762.4999999757736   
Generation-3981     Average fitness: 758.7553459243697       Best fitness: 762.4999999757736   
Generation-3982     Average fitness: 748.2473778519715       Best fitness: 762.4999999757736   
Generation-3983     Average fitness: 744.0824405222568       Best fitness: 762.4999999757736   
Generation-3984     Average fitness: 758.7978195049452       Best fitness: 762.4999999757736   
Generation-3985     Average fitness: 760

#### Disscussion
Implementing the single-objective and constrained optimisation function requires only updating the fitness function and the representation of the real values. To minimise the both functions, the score is subtracted from the 'padding' since the worst chromosome is evaluated as the smallest number compared to maximising the function, which is just calculating the function. This notebook contains implementations for maximising and minimising both functions.<br>

The representation of the real numbers x and y is a single bitstring encoded by concetenating 2 bitstrings (for x and y), each of length 50, so the resulting bitstring has a length of 100 and is decoded by splitting the bitstring in the middle (since the numbers are of equal size), and further decoding by using fixed-point representation with a min and max value used to scale the decimal value.<br>

Since the implementation uses 50 bits for each number, the implementation is extremely precise with a resolution of:

In [18]:
print("Ackley function (x and y):", (5 - -5)/(2**50 - 1))
print("\nRosenbrock function (x):  ", (1.5 - -1.5)/(2**50 - 1))
print("Rosenbrock function (y):  ", (2.5 - -0.5)/(2**50 - 1))

Ackley function (x and y): 8.88178419700126e-15

Rosenbrock function (x):   2.664535259100378e-15
Rosenbrock function (y):   2.664535259100378e-15


With the resolution for the Ackley function, minimising typically converges before 100-200 generations. On the other hand, maximising can converge up to 5,000 generations and possibly higher. The Rosenbrock function converges higher at around 3,000-4,000 generations.<br>

The constrained Rosenbrock function contains local minima, which the results can see. Occasionally, the best fitness can get stuck at around 507 for many generations before increasing to 762.<br>

Increasing the accuracy of the representation (increasing the number of bits per number) will increase the number of generations it takes to converge. Both functions reach close to the min/max values reasonably quickly and uses the rest of the generations to get a more precise result.<br>

Using the optimal hyper-parameters, the results could have been better, and the final values were far from the min/max values; increasing the generation size to a very high number helped to identify what parameters needed to be changed. It showed that the GA was converging at an early generation. Increasing the population size also helped when getting a more accurate result. Strangely enough, the mutation rate of 0.02 for the Rosenbrock function did not result in a very close value, and a mutation rate of 0.1 gets the value closer to the min/max value. This indicates that the GA may converge at a local minimum; the extra mutations help to escape the local minimums.<br>

Improvements to the solution include changing the crossover operation. For example, since each chromosome contains two values, it may be more appropriate to crossover each of the two chromosomes separately and recombine rather than performing the crossover on the whole chromosome. Alternatively, changing the representation so that the separate x and y values are not concatenated but interleaved and keeping the initial crossover implementation. Other improvements include increasing the population size or the number of generations to explore the search space more thoroughly.

## 4. Free choice (interesting task for you)
### Raid composition problem:
Contains overwritten methods for fitness() and decodeChromosome().<br>
It also contains new methods:<br><br>
__*classSetup()*__<br>
Setup the classes and the class list.

__*bossSetup()*__<br>
Setup for the bosses and select a random boss.

__*printCustomGAResults(run)*__<br>
Prnts the results of the run.

__*printRaidGroup(raidGroup)*__<br>
Prints the composition of the raid group.

__*printRaidGroupStats(damage, healing, tankHealth)*__<br>
Prints the statistics of the group.

In [19]:
#Variables to decode chromosomes
numberOfBitsPerNumber = 4
numberOfMembers = 15
numberOfBits = numberOfBitsPerNumber * numberOfMembers


class Class:
    def __init__(self, name, role, damage, health, healing):
        self.name = name
        self.role = role
        self.damage = damage
        self.health = health
        self.healing = healing
    
class Boss:
    def __init__(self, name, damage, health):
        self.name = name
        self.damage = damage
        self.health = health
        

def fitness(chromosome):
    """Evaluates the fitness score of a chromosome, which is the biggest total damage with some
    contraints:
    Group must consist at least 1 tank and 1 healer
    Group's total healing and total tanks health must both be higher than boss damage
    Penalty applied if 3 or more of the same class is used.
    
    Returned score is the total damage of the group multiplied by the penalty.
    """
    
    global fitnessEvaluationCount
    fitnessEvaluationCount += 1
    
    
    raidGroup = decodeChromosome(chromosome)
    
    damage = 0
    healing = 0
    tanks = 0
    tanksHealth = 0
    healers = 0
    classCounts = {}
    
    #Calculate raid group stats
    for member in raidGroup:
        damage += member.damage
        healing += member.healing
        
        if (member.role == "Tank"):
            tanks += 1
            tanksHealth += member.health
        if (member.role == "Healer"):
            healers += 1
            
        if member.name in classCounts:
            classCounts[member.name] += 1
        else:
            classCounts[member.name] = 1
    
    
    #Contraints
    if tanks < 1 or healers < 1:
        return 1
    if healing < boss.damage and tanksHealth < boss.damage:
        return 2
    elif healing < boss.damage or tanksHealth < boss.damage:
        return 3
    
    #Class penalty
    multipleClassPenalty = 1
    for count in classCounts.values():
        if count >= 3:
            multipleClassPenalty -= (0.03 * (count - 2)**2 )
    
    return damage * multipleClassPenalty if damage * multipleClassPenalty > 0 else 4


def decodeChromosome(chromosome):
    """Decodes the chromosome into a list of classes representing a raid group composition."""
    
    raidGroup = []
    
    #For each number in the chromosome
    for i in range(0, numberOfBits, numberOfBitsPerNumber):
        binaryNumber = chromosome[i:i+numberOfBitsPerNumber]
        
        index = int(binaryNumber, 2) #Convert binary to decimal
        
        #Wrap around bits larger than the number of classes using modulus 
        raidGroup.append(classes[index % len(classes)])
    
    return raidGroup


def classSetup():
    """Setup the classes and the class list."""
    
    warrior = Class("Warrior", "Tank", 400, 7000, 0)
    paladin = Class("Paladin", "Tank", 300, 6000, 500)
    knight = Class("Knight", "Damage", 700, 5000, 700)
    mage = Class("Mage", "Damage", 1600, 3000, 0)
    ranger = Class("Ranger", "Damage", 1300, 3500, 0)
    assasin = Class("Assasin", "Damage", 1200, 4000, 0)
    warlock = Class("Warlock", "Damage", 1400, 3000, 0)
    shaman = Class("Shaman", "Healer", 450, 2500, 1500)
    monk = Class("Monk", "Healer", 150, 2700, 2500)
    druid = Class("Druid", "Healer", 100, 4000, 2300)
    priest = Class("Priest", "Healer", 50, 2300, 3200)
    
    global classes
    classes = [warrior, paladin, knight, mage, ranger, assasin, warlock, shaman, monk, druid, priest]

def bossSetup():
    """Setup for the bosses and select a random boss."""
    
    ultrex = Boss("Ultrex", 23000, 1200000)
    hydra = Boss("Hydra", 20000, 1800000)
    dragon = Boss("Dragon", 10000, 2500000)
    cyclops = Boss("Cyclops", 3000, 1750000)
    medusa = Boss("Medusa", 15000, 2000000)
    namelessKing = Boss("The Nameless King", 24000, 3000000)

    bosses = [ultrex, hydra, dragon, cyclops, medusa, namelessKing]

    global boss
    boss = bosses[rnd.randint(0, len(bosses) - 1)]


def printCustomGAResults(run):
    """Prints the results of the run."""
    
    print("Results:")
    print("Fitness evaluations:", run[2])
    print("Best fitness:", run[1])
    print("Best solution found at generation: {}/{}".format(run[0], numberOfGenerations))
    print("Best chromosome:", run[3])

def printRaidGroup(raidGroup):
    """Prints the composition of the raid group."""
    
    healing = 0
    tankHealth = 0
    damage = fitness(run[3])
    print("\nFinal raid composition for (" + boss.name + "):")
    print("Role:    Class:")
    for member in raidGroup:
        healing += member.healing
        if (member.role == "Tank"):
            tankHealth += member.health
        print("{:8} {}".format(member.name, member.role))
    
    printRaidGroupStats(damage, healing, tankHealth)

def printRaidGroupStats(damage, healing, tankHealth):
    """Prints the statistics of the group."""
    
    print("\nTotal damage per second (including penalty): {:,.2f}".format(damage))
    print("Total healing: {:,}".format(healing))
    print("Total tank health: {:,}".format(tankHealth))
    print("\nBoss damage: {:,}".format(boss.damage))
    print("Boss health: {:,}".format(boss.health))
    print("Time to kill boss: {:.2f} minutes".format((boss.health / damage) / 60))

    

classSetup()
bossSetup()


#Hyper-parameters
populationSize = 25
numberOfGenerations = 2000
crossoverRate = 1
mutationRate = 0.1
numberOfTournament = 2

#Run GA
startTime = timeit.default_timer()
run = runGA(displayOutput = False, displayASCII = False)
timeElapsed = timeit.default_timer() - startTime


printCustomGAResults(run)
print("Time taken to run: {:.2f} seconds".format(timeElapsed))

#Get the final raid composition
finalRaidGroup = decodeChromosome(run[3])
finalRaidGroup.sort(key=lambda x: (x.role, x.name)) #Sort by role then name
printRaidGroup(finalRaidGroup)

Results:
Fitness evaluations: 50026
Best fitness: 5499.0
Best solution found at generation: 264/2000
Best chromosome: 110010000111101010001110000010011000100110111100101011101010
Time taken to run: 0.69 seconds

Final raid composition for (The Nameless King):
Role:    Class:
Mage     Damage
Mage     Damage
Druid    Healer
Druid    Healer
Monk     Healer
Monk     Healer
Monk     Healer
Priest   Healer
Priest   Healer
Priest   Healer
Shaman   Healer
Paladin  Tank
Paladin  Tank
Warrior  Tank
Warrior  Tank

Total damage per second (including penalty): 5,499.00
Total healing: 24,200
Total tank health: 26,000

Boss damage: 24,000
Boss health: 3,000,000
Time to kill boss: 9.09 minutes


#### Raid composition problem

A raid group is needed to kill a range of six different bosses. Each boss has a set health and damage and is randomly selected at the start of the problem. These bosses are:<br>

| Boss name | Damage  | Health    |
| :-        | :-      | :-        |
| Ultrex    | 23,000  | 1,200,000 |
| Hydra     | 20,000  | 1,800,000 |
| Dragon    | 10,000  | 2,500,000 |
| Cyclops   | 3,000   | 1,750,000 |
| Medusa    | 15,000  | 2,000,000 |
| The Nameless King | 20,000 | 3,000,000 |


<br><br>The raid group needs to consist of 15 members, and each member can be any one of the below classes:

| Class  | Role  | Damage| Health|Healing|
| :-     | :-    | :-    | :-    | :-    |
| Warrior| Tank  | 400   | 7,000 | 0     |
| Paladin| Tank  | 300   | 6,000 | 500   |
| Knight | Damage| 700   | 5,000 | 700   |
| Mage   | Damage| 1,600 | 3,000 | 0     |
| Ranger | Damage| 1,300 | 3,500 | 0     |
| Assasin| Damage| 1,200 | 4,000 | 0     |
| Warlock| Damage| 1,400 | 3,000 | 0     |
| Shaman | Healer| 450   | 2,500 | 1,500 |
| Monk   | Healer| 150   | 2,700 | 2,500 |
| Druid  | Healer| 100   | 4,000 | 2,300 |
| Priest | Healer| 50    | 2,300 | 3,200 |

<br>The problem is that a raid group with the highest damage should be selected with the below requirements:
- There must be at least one healer
- There must be at least one tank
- The group's total healing is above the boss's damage
- The total tanks health is above the bosses damage

<br>
A penalty is applied to the damage if there are more than three of the same class; this penalty increases with the number of the same class. So, for example, if there are three of the same class, only a 0.03 penalty is applied; however, if there are five, the penalty is increased to 0.27, diversifying the class usage.<br>

The fitness function returns a score based on the group's total damage. However, the requirements are checked first, and a score is returned based on how many requirements have been met. For example:
- One is returned if there are less than one tank or healer.
- Two is returned if the healing AND tank health is less than the boss's damage.
- Three is returned if the healing OR tank health is less than the boss damage.
- Four is returned if the multiple-class penalty is below zero.

This results in a ranking based on how close a group is to passing the requirements. If the above requirements are passed, the damage multiplied by the penalty is returned.<br><br>

Each chromosome represents a list of indices refering to a class in the classes list. At least four bits are required to represent nine values (number of classes) which means there are binary values left over as nine is not a power of two. So, the binary number is reduced to the range 0-8 using the modulus operator, this results in wrap around with any binary number larger than eight.<br>

To find a group with enough healing/ tank health to defeat high-damage bosses, the GA typically requires about 2000 generations. However, lower-damage bosses converge quickly since covering the healing/ tank health required is easier. In both cases, there are still enough generations to refine the solution to get the group with the highest damage. Due to the small number of bits, the GA operates reasonably quickly.

The raid groups formed from the GA are different for each boss showing that using a specific selection of classes will be more beneficial than others for each boss. For example, using five tanks and ten healers is not ideal if the boss only does 3,000 damage.<br>



### Jigsaw problem:
Contains overwritten methods for fitness() and decodeChromosome().<br>
It also contains new methods:<br><br>

__*piecesSetup()*__<br>
Setup the pieces list incrementally left-to-right, top-to-bottom.

__*addPieceNeighbours()*__<br>
Add the correct neighbours to each piece (-1 for edge pieces).

__*getNeighbours(board, x, y)*__<br>
Get the neighbours of a piece on the 'board' using the 'x' and 'y' position. Initially sets all neighbours to -1 and updates if there is a neighbour at that position.

__*printBoard(chromosome)*__<br>
Prints the board that the chromosome represents.

__*printCorrectBoard()*__<br>
Prints the correct board.

__*printCustomGAResults(run)*__<br>
Print the results of the run.

In [21]:
#Variables to decode chromosomes
numberOfBitsPerNumber = 6
width = 8
height = 8
numberOfNumbers = width * height
numberOfBits = numberOfBitsPerNumber * numberOfNumbers


class Piece:
    def __init__(self, value):
        self.value = value
        
    def setUp(self, up):
        self.up = up
    def setDown(self, down):
        self.down = down
    def setLeft(self, left):
        self.left = left
    def setRight(self, right):
        self.right = right

        
def fitness(chromosome):
    """Evaluates the fitness score of a chromosome, which is the number of correct neighbours of each
    piece.
    
    For example:
    0 1 3
    4 6 5
    Piece 0 increases the score by 4 (since each neighbour is correct, -1 for edges)
    Piece 5 increases the score by 3 (since its right should be 6 not -1)"""
    
    global fitnessEvaluationCount
    fitnessEvaluationCount += 1
    
    board = decodeChromosome(chromosome)
    score = 0
    
    #For each piece in the board
    for y in range(height):
        for x in range(width):
            
            neighbours = getNeighbours(board, x, y)
            
            piece = board[x + y * width]
            
            if piece.up == neighbours[0]:
                score += 1
            if piece.down == neighbours[1]:
                score += 1
            if piece.left == neighbours[2]:
                score += 1
            if piece.right == neighbours[3]:
                score += 1
                
    return score

def decodeChromosome(chromosome):
    """Decodes the chromosome into a list of indexes of the pieces list which represents a board."""
    
    board = []
    
    #For each number in the chromosome
    for i in range(0, numberOfBits, numberOfBitsPerNumber):
        binaryNumber = chromosome[i:i+numberOfBitsPerNumber]
        
        index = int(binaryNumber, 2) #Convert binary to decimal
        
        board.append(pieces[index])
    
    return board


def piecesSetup():
    """Setup the pieces list incrementally left-to-right, top-to-bottom."""
    
    global pieces
    pieces = []

    count = 0
    for y in range(height):
        for x in range(width):
            pieces.append(Piece(count))
            count += 1
            
def addPieceNeighbours():
    """Add the correct neighbours to each piece (-1 for edge pieces)."""
    
    for y in range(height):
        for x in range(width):
            neighbours = getNeighbours(pieces, x, y)
            
            piece = pieces[x + y * width]
            piece.setUp(neighbours[0])
            piece.setDown(neighbours[1])
            piece.setLeft(neighbours[2])
            piece.setRight(neighbours[3])
            
def getNeighbours(board, x, y):
    """Get the neighbours of a piece on the 'board' using the 'x' and 'y' position.
    Initially sets all neighbours to -1 and updates if there is a neighbour at that position."""
    
    pieceUp = -1
    pieceDown = -1
    pieceLeft = -1
    pieceRight = -1
    
    if y - 1 > 0:
        pieceUp = board[x + (y - 1) * width].value
    if y + 1 < height - 1:
        pieceDown = board[x + (y + 1) * width].value
    if x - 1 > 0:
        pieceLeft = board[x - 1 + y * width].value
    if x + 1 < width or x != width - 1:
        pieceRight = board[x + 1 + y * width].value
        
    return (pieceUp, pieceDown, pieceLeft, pieceRight)


def printBoard(chromosome):
    """Prints the board that the chromosome represents."""
    
    print("\nBest board:")
    bestBoard = decodeChromosome(chromosome)
    for y in range(height):
        for x in range(width):
            print("{:3}".format(bestBoard[x + y * width].value), end=" ")
        print()
    print()
    
def printCorrectBoard():
    """Prints the correct board."""
    
    print("Correct board:")
    count = 0      
    for x in range(width):
        for y in range(height):
            print("{:3}".format(count), end=" ")
            count += 1
        print()
    print()

def printCustomGAResults(run):
    """Print the results of the run."""
    
    print("Results:")
    print("Fitness evaluations:", run[2])
    print("Best fitness: {}/{}".format(run[1], numberOfNumbers * 4))
    print("Best solution found at generation: {}/{}".format(run[0], numberOfGenerations))
    print("Best chromosome:", run[3])



piecesSetup()
addPieceNeighbours()


#Hyper-parameters
populationSize = 100
numberOfGenerations = 40000
crossoverRate = 1
mutationRate = 0.025
numberOfTournament = 4

#Run GA
startTime = timeit.default_timer()
run = runGA(displayOutput = True, displayASCII = False)
timeElapsed = timeit.default_timer() - startTime


printCustomGAResults(run)
print("Time taken to run: {:.2f} seconds".format(timeElapsed))

printBoard(run[3])
printCorrectBoard()

Start of GA

Hyper-parameters:
Population size: 100
Number of generations: 40000
Number of individuals in tournament selection: 4
Crossover rate: 1
Mutation rate (per bit): 0.025 

Generation-0        Average fitness: 22.92                   Best fitness: 30                  
Generation-1        Average fitness: 27.97                   Best fitness: 36                  
Generation-2        Average fitness: 31.87                   Best fitness: 39                  
Generation-3        Average fitness: 34.77                   Best fitness: 43                  
Generation-4        Average fitness: 37.57                   Best fitness: 43                  
Generation-5        Average fitness: 39.83                   Best fitness: 48                  
Generation-6        Average fitness: 41.72                   Best fitness: 49                  
Generation-7        Average fitness: 44.38                   Best fitness: 52                  
Generation-8        Average fitness: 45.7          

Generation-125      Average fitness: 85.14                   Best fitness: 90                  
Generation-126      Average fitness: 85.27                   Best fitness: 90                  
Generation-127      Average fitness: 85.24                   Best fitness: 90                  
Generation-128      Average fitness: 85.31                   Best fitness: 90                  
Generation-129      Average fitness: 85.37                   Best fitness: 90                  
Generation-130      Average fitness: 85.45                   Best fitness: 90                  
Generation-131      Average fitness: 85.42                   Best fitness: 90                  
Generation-132      Average fitness: 85.46                   Best fitness: 90                  
Generation-133      Average fitness: 85.67                   Best fitness: 90                  
Generation-134      Average fitness: 85.63                   Best fitness: 90                  
Generation-135      Average fitness: 85.

Generation-245      Average fitness: 93.52                   Best fitness: 99                  
Generation-246      Average fitness: 93.78                   Best fitness: 99                  
Generation-247      Average fitness: 93.73                   Best fitness: 99                  
Generation-248      Average fitness: 93.68                   Best fitness: 99                  
Generation-249      Average fitness: 93.81                   Best fitness: 99                  
Generation-250      Average fitness: 93.85                   Best fitness: 99                  
Generation-251      Average fitness: 93.91                   Best fitness: 99                  
Generation-252      Average fitness: 93.86                   Best fitness: 99                  
Generation-253      Average fitness: 94.02                   Best fitness: 99                  
Generation-254      Average fitness: 94.03                   Best fitness: 99                  
Generation-255      Average fitness: 94.

Generation-331      Average fitness: 99.39                   Best fitness: 107                 
Generation-332      Average fitness: 99.34                   Best fitness: 107                 
Generation-333      Average fitness: 99.35                   Best fitness: 107                 
Generation-334      Average fitness: 99.58                   Best fitness: 107                 
Generation-335      Average fitness: 99.58                   Best fitness: 107                 
Generation-336      Average fitness: 99.59                   Best fitness: 107                 
Generation-337      Average fitness: 99.75                   Best fitness: 107                 
Generation-338      Average fitness: 99.89                   Best fitness: 107                 
Generation-339      Average fitness: 99.99                   Best fitness: 107                 
Generation-340      Average fitness: 100.06                  Best fitness: 107                 
Generation-341      Average fitness: 100

Generation-421      Average fitness: 103.43                  Best fitness: 109                 
Generation-422      Average fitness: 103.5                   Best fitness: 109                 
Generation-423      Average fitness: 103.51                  Best fitness: 109                 
Generation-424      Average fitness: 103.52                  Best fitness: 109                 
Generation-425      Average fitness: 103.55                  Best fitness: 109                 
Generation-426      Average fitness: 103.45                  Best fitness: 109                 
Generation-427      Average fitness: 103.61                  Best fitness: 109                 
Generation-428      Average fitness: 103.44                  Best fitness: 109                 
Generation-429      Average fitness: 103.55                  Best fitness: 109                 
Generation-430      Average fitness: 103.66                  Best fitness: 109                 
Generation-431      Average fitness: 103

...

Generation-39500    Average fitness: 161.81                  Best fitness: 164                 
Generation-39501    Average fitness: 162.06                  Best fitness: 164                 
Generation-39502    Average fitness: 162.21                  Best fitness: 164                 
Generation-39503    Average fitness: 162.07                  Best fitness: 164                 
Generation-39504    Average fitness: 162.1                   Best fitness: 164                 
Generation-39505    Average fitness: 161.97                  Best fitness: 164                 
Generation-39506    Average fitness: 162.12                  Best fitness: 164                 
Generation-39507    Average fitness: 162.07                  Best fitness: 164                 
Generation-39508    Average fitness: 161.95                  Best fitness: 164                 
Generation-39509    Average fitness: 161.98                  Best fitness: 164                 
Generation-39510    Average fitness: 161

Generation-39591    Average fitness: 161.95                  Best fitness: 164                 
Generation-39592    Average fitness: 161.71                  Best fitness: 164                 
Generation-39593    Average fitness: 161.97                  Best fitness: 164                 
Generation-39594    Average fitness: 162.01                  Best fitness: 164                 
Generation-39595    Average fitness: 162.02                  Best fitness: 164                 
Generation-39596    Average fitness: 161.99                  Best fitness: 164                 
Generation-39597    Average fitness: 162.04                  Best fitness: 164                 
Generation-39598    Average fitness: 161.94                  Best fitness: 164                 
Generation-39599    Average fitness: 162.16                  Best fitness: 164                 
Generation-39600    Average fitness: 161.91                  Best fitness: 164                 
Generation-39601    Average fitness: 161

Generation-39716    Average fitness: 162.08                  Best fitness: 164                 
Generation-39717    Average fitness: 162.1                   Best fitness: 164                 
Generation-39718    Average fitness: 161.96                  Best fitness: 164                 
Generation-39719    Average fitness: 161.97                  Best fitness: 164                 
Generation-39720    Average fitness: 162.12                  Best fitness: 164                 
Generation-39721    Average fitness: 162.04                  Best fitness: 164                 
Generation-39722    Average fitness: 161.98                  Best fitness: 164                 
Generation-39723    Average fitness: 161.95                  Best fitness: 164                 
Generation-39724    Average fitness: 162.03                  Best fitness: 164                 
Generation-39725    Average fitness: 161.79                  Best fitness: 164                 
Generation-39726    Average fitness: 162

Generation-39807    Average fitness: 162.05                  Best fitness: 164                 
Generation-39808    Average fitness: 162.02                  Best fitness: 164                 
Generation-39809    Average fitness: 162.16                  Best fitness: 164                 
Generation-39810    Average fitness: 162.1                   Best fitness: 164                 
Generation-39811    Average fitness: 162.11                  Best fitness: 164                 
Generation-39812    Average fitness: 161.97                  Best fitness: 164                 
Generation-39813    Average fitness: 162.17                  Best fitness: 164                 
Generation-39814    Average fitness: 161.93                  Best fitness: 164                 
Generation-39815    Average fitness: 162.04                  Best fitness: 164                 
Generation-39816    Average fitness: 161.94                  Best fitness: 164                 
Generation-39817    Average fitness: 162

Generation-39925    Average fitness: 162.11                  Best fitness: 164                 
Generation-39926    Average fitness: 162.19                  Best fitness: 164                 
Generation-39927    Average fitness: 162.19                  Best fitness: 164                 
Generation-39928    Average fitness: 162.02                  Best fitness: 164                 
Generation-39929    Average fitness: 162.15                  Best fitness: 164                 
Generation-39930    Average fitness: 162.1                   Best fitness: 164                 
Generation-39931    Average fitness: 162.09                  Best fitness: 164                 
Generation-39932    Average fitness: 162.11                  Best fitness: 164                 
Generation-39933    Average fitness: 161.99                  Best fitness: 164                 
Generation-39934    Average fitness: 162.09                  Best fitness: 164                 
Generation-39935    Average fitness: 161

#### Basic jigsaw problem
A jigsaw does not seem like a large combinatorial optimisation problem. However, assuming edge pieces can be placed anywhere, the maths for the permutations of all the pieces is the factorial of the number of pieces:<br><br>
8 x 8 = 64 pieces (height x width)<br>
64! = 1.2688693e+89<br><br>
Which is an astronomically large number for just an eight-by-eight jigsaw. (this was something I did not realise at the time)<br><br>

A correct board is one that each consecutive piece is one more than the previous (starting at zero), and is arranged left-to-right and top-to-bottom. A board contains 64 pieces, each containing five integer values: the value of the piece and the value above, below and to the left and right, using -1 to indicate an edge piece. For example:<br>
0 1 2<br>
3 4 5<br>
6 7 8<br>
Piece '4' has neighbours of 1, 5, 7 and 3 for the top, right, bottom and left, respectively, and piece '0' has neighbours of -1, 1, 3, -1 for the top, right, bottom and left, respectively.<br>

Since the implementation for this problem is very rudimentary, it assumes that the pieces cannot be rotated, can be placed more than once and can be placed anywhere. The solutions generated by this GA act and more of a guide than a solution generator since it is extremely challenging to produce a perfect solution.<br>

A list of pieces 'pieces' is created at the start of the GA, which represents a correct board, and is used when decoding a chromosome. Each chromosome consists of 64 numbers (width x height) encoded using six bits each and since 64 is a power of two then no extra wrapping/clipping or scaling is needed. Each of the 64 numbers represents an index of the initial correct board.<br>

An obvious fitness function would count the number of pieces in the correct position returning 64 for the perfect solution; however, if a person was doing a jigsaw, they do not have this information. Therefore, the implemented fitness function calculates how many pieces have the correct neighbours (+1 for each), e.g. how many pieces are connected; this more closely relates to how a person would solve a jigsaw. The perfect solution would have a fitness score of 256.<br>

The GA runs very slowly as the fitness function must iterate through each board and uses a list access, the function must also run through a lot of generations due to the fact that the search space is extremely large. The GA reaches around ~100 fitness score fairly quickly (around 400 generations), however, after this point there are many generations between improvements. The resulting board from 40,000 generations which takes ~four minutes to run, has a fitness score of 164, comparing this board to the correct board some similarities can be seen, such as the numbers along the edges are mostly correct, apart from the order of some of them, the second row is exactly correct, and there are occationally blocks within the output where the pieces do have some of the correct neighbours, but may not necessarily be in the correct position.<br>

An idea to improve the GA was to initially shuffle the list of pieces and swap two pieces for the crossover. Although this is moving away from GA, changing the crossover operator may also result in different results.

## 5. Self-assesment
The structure of this notebook is very well thought out. It is well-documented, developed, and refactored to an extreme-programming style.

#### Steady-state GA
My steady-state GA has been developed to allow the rest of the notebook to use the same method to run subsequent GAs with overwritten fitness() methods and different binary representation variables for encoding/decoding chromosomes. It implements all operations that a GA requires (crossover, mutation, selection, and initialPopulation) and starts with default hyper-parameters that have been discussed in the lectures. It can also, depending on parameters, display statistics of each generation and the statistics at the end of the GA.<br>

#### ASCII art
The ASCII art task implementation meets the marking criteria as it successfully produces ASCII art output that is, usually, a perfect solution. The implementation consists of a fitness function that scores chromosomes based on the specification and variables to encode/decode chromosomes. The best chromosome is printed out as an 'image' upon completion.

#### Hyper-parameter Analysis
My hyper-parameter analysis is very in-depth, I created a method that runs the ASCII GA many times, and since the GA can return the results, it can then average those results, which provides an excellent quantitative measure for how good or bad a specific change in hyper-parameter is. I analyse each parameter separately and analyse values above and below the default values. After each hyper-parameter has been tested, I discuss the results and identify the best value for that parameter.<br>

Once all hyper-parameters have been analysed, I compare the default parameters to the optimised parameters, in which there is a distinct improvement.

#### Fitness function
For my fitness function section, I selected the Ackley function and the Rosenbrock function constrained with a cubic and a line. My implementation contains simulations for both the minimum and maximum of the functions, and the results of each generation are displayed and referenced in the discussion observations section, located after all four implementations.<br>

The discussion answers all the questions, each in good detail. For example, when discussing precision, the resolution is calculated and explained. The discussion also highlights some interesting observations made after running all the functions.

#### Free choice (interesting task for you)
The combinatorial problems I initially thought of were variations of existing problems, such as the knapsack and travelling salesman problems. But, I wanted to come up with a new exciting problem. I thought about doing a sorting problem; however, sorting algorithms are very efficient. So, instead, I came up with two problems because I enjoyed making the first one.

I play World of Warcraft, and I had the idea to make a raid group composition to select the best classes for specific bosses with specific requirements for the first problem. For the second problem, I thought about using a GA to tackle a huge combinatorial problem to see how good the solutions are, so I chose a jigsaw. However, I only realised during development that this is a tough problem to solve, so my implementation is fundamental and does not fully capture the problem.<br>

Each problem is well documented and structured, and both problems are very different from each other, requiring specific logic. Discussions are also made after the results of each problem.